In [1]:
import numpy as np, matplotlib.pyplot as plt
from numpy import *
import pylab
import scipy as scipy
from scipy.io import wavfile
from numpy.fft import *
import scipy.signal as signal
from matplotlib.pyplot import *
import IPython
import cmath

In [2]:
samplerate, sound = wavfile.read('crumble.wav')
IPython.display.display(IPython.display.Audio(sound, rate=samplerate))

# Part 1 Static sources using ITD/ILD cues

## a)  Straight ahead

In [3]:
left_channel = sound
right_channel = sound

output = np.array([left_channel, right_channel])

IPython.display.display(IPython.display.Audio(output, rate=samplerate))

## b)  45 degrees to the left

In [4]:
delay = 20 #delay in samples
left_channel = sound

right_channel = np.append(np.zeros(delay), sound)
right_channel = (right_channel[:-delay])*0.85

output = np.array([left_channel, right_channel])

IPython.display.display(IPython.display.Audio(output, rate=samplerate))

## c) 80 degrees to the right

In [5]:
# Part 3 80 degrees to the right
delay = 28
right_channel = sound

left_channel = np.append(np.zeros(delay), sound)
left_channel = (left_channel[:-delay])*0.7337

output = np.array([left_channel, right_channel])

IPython.display.display(IPython.display.Audio(output, rate=samplerate))

## d) 160 degrees to the left

In [6]:
delay = 10 #delay in samples
left_channel = sound

right_channel = np.append(np.zeros(delay), sound)
right_channel = (right_channel[:-delay])*0.933

output = np.array([left_channel, right_channel])

IPython.display.display(IPython.display.Audio(output, rate=samplerate))

# Part 2 Static sources using HRTFs 

## Given Code

In [7]:
def load_hrtf( ad, ed):
    # Return the HRTFs for a given azimuth and elevation
    #  function h,a,e = load_hrtf( ad, ed)
    #
    # Inputs:
    #   ad  is the azimuth to use in degrees (0 is front)
    #   ed  is the elevation to use in degrees (0 is level with ears)
    #
    # Output:
    #   l,r two 128pt arrays, first is left ear HRTF, second is right ear HRTF



    # Path where the HRTFs are
    p = 'hrtf/compact/'

    # Get nearest available elevation
    e = max( -40, min( 90, 10*(ed//10)))

    # Get nearest available azimuth
    ad = remainder( ad, 360)
    if ad > 180:
        ad = ad-360
    if ad < 0:
        a = abs( ad)
        fl = 1
    else:
        a = ad
        fl = 0
    a = max( 0, min( 180, 5*(a//5)))

    # Load appropriate response
    h = fromfile( '%s/elev%d/H%de%.3da.dat' % (p, e, e, a), dtype='>i2').astype( 'double')/32768
    if fl:
        return h[1::2],h[::2]
    else:
        return h[::2],h[1::2]

## Function to get hrtf output

In [8]:
def get_hrtf_sound(sound, azimuth, elev):
    hrtf = load_hrtf(azimuth, elev)
    left_channel = signal.convolve(hrtf[0], sound)
    right_channel = signal.convolve(hrtf[1], sound)

    output = np.array([left_channel, right_channel])

    IPython.display.display(IPython.display.Audio(output, rate=samplerate))

## Straight ahead

In [9]:
get_hrtf_sound(sound, 0, 0)

## 45 degrees to the left

In [10]:
get_hrtf_sound(sound, 315, 0)

## 80 degrees to the right

In [11]:
get_hrtf_sound(sound, 80, 0)

## 160 degrees to the left

In [12]:
get_hrtf_sound(sound, 200, 0)

# Part 3

In [13]:
def stft(input_sound, dft_size, hop_size, zero_pad, window):

    # Forward tranform
    if(input_sound.ndim is 1):
        # Zero Pad the signal
        length_input_sound = len(input_sound)
        remainder = (length_input_sound - dft_size)%hop_size
        padded_input = append(input_sound,zeros(hop_size-remainder))
        padded_input = append(zeros(dft_size), padded_input)

        # Calculcate FFTs using analysis(hamming) window
        X = np.array([np.fft.rfft(window*padded_input[i:i+dft_size], dft_size + zero_pad) 
                        for i in range(0, len(padded_input)-dft_size+1, hop_size)])
        X = X.T
        
        return X
        
    # Inverse transform
    else:
        #Restore original shape
        waveform = np.zeros(dft_size + (input_sound.shape[1]-1)*hop_size)
        X = input_sound.T
        
        for n,i in enumerate(range(0, len(waveform)-dft_size-zero_pad+1, hop_size)):
            waveform[i:i+dft_size+zero_pad] += np.real(np.fft.irfft(X[n]))
           
            
        for i in range(0, len(waveform)-dft_size + 1, hop_size):
            waveform[i:i+dft_size] = waveform[i:i+dft_size]
        
        return waveform

In [14]:
freq_sound = stft(sound, 128, 128, 128, np.ones(128))
freq_sound = freq_sound.T

angles = np.linspace(0, 360, 581)
angles2 = np.linspace(360, 0, 582)
angles = np.append(angles, angles2)

left_channel_matrix = np.zeros((1163, 129), dtype = complex_)
right_channel_matrix = np.zeros((1163, 129), dtype= complex_)

In [15]:
for i in range(1163):
    frame = freq_sound[i]
    angle = angles[i]
    hrtf = load_hrtf(angle, 0)
    
    left_fourier_hrtf = np.fft.rfft(hrtf[0], 256)
    right_fourier_hrtf = np.fft.rfft(hrtf[1], 256)
    
    left_channel = np.multiply(left_fourier_hrtf, frame)
    right_channel = np.multiply(right_fourier_hrtf, frame)
    
    left_channel_matrix[i] = left_channel
    right_channel_matrix[i] = right_channel
    
left_channel_matrix = left_channel_matrix.T
right_channel_matrix = right_channel_matrix.T

In [16]:
left_wave = stft(left_channel_matrix, 128, 128, 128, np.ones(128))
right_wave = stft(right_channel_matrix, 128, 128, 128, np.ones(128))

In [17]:
output = np.array([left_wave, right_wave])
print("Final Dynamic Sound(Starts from right, goes to left and then back to the right)")
IPython.display.display(IPython.display.Audio(output, rate=samplerate))

Final Dynamic Sound(Starts from right, goes to left and then back to the right)
